In [1]:
import pandas as pd
from prophet import Prophet

In [2]:
df = pd.read_csv("/content/NIFTY 50_Data.csv")

In [3]:
df.head()

Date      Open      High       Low     Close
0  24 Feb 2023  17591.35  17599.75  17421.80  17465.80
1  23 Feb 2023  17574.65  17620.05  17455.40  17511.25
2  22 Feb 2023  17755.35  17772.50  17529.45  17554.30
3  21 Feb 2023  17905.80  17924.90  17800.30  17826.70
4  20 Feb 2023  17965.55  18004.35  17818.40  17844.60

In [4]:
df.rename(columns = {'Date':'ds'}, inplace = True)

In [5]:
df['ds'] = pd.to_datetime(df['ds'])

In [6]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 5761 entries, 0 to 5760
Data columns (total 5 columns):
 #   Column  Non-Null Count  Dtype         
---  ------  --------------  -----         
 0   ds      5761 non-null   datetime64[ns]
 1   Open    5761 non-null   float64       
 2   High    5761 non-null   float64       
 3   Low     5761 non-null   float64       
 4   Close   5761 non-null   float64       
dtypes: datetime64[ns](1), float64(4)
memory usage: 225.2 KB


In [7]:
df.rename(columns = {'Close':'y'}, inplace = True)

In [8]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 5761 entries, 0 to 5760
Data columns (total 5 columns):
 #   Column  Non-Null Count  Dtype         
---  ------  --------------  -----         
 0   ds      5761 non-null   datetime64[ns]
 1   Open    5761 non-null   float64       
 2   High    5761 non-null   float64       
 3   Low     5761 non-null   float64       
 4   y       5761 non-null   float64       
dtypes: datetime64[ns](1), float64(4)
memory usage: 225.2 KB


In [9]:
df=df.drop(['Open', 'High', 'Low'] , axis=1)

In [10]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 5761 entries, 0 to 5760
Data columns (total 2 columns):
 #   Column  Non-Null Count  Dtype         
---  ------  --------------  -----         
 0   ds      5761 non-null   datetime64[ns]
 1   y       5761 non-null   float64       
dtypes: datetime64[ns](1), float64(1)
memory usage: 90.1 KB


In [11]:
df.head()

ds         y
0 2023-02-24  17465.80
1 2023-02-23  17511.25
2 2023-02-22  17554.30
3 2023-02-21  17826.70
4 2023-02-20  17844.60

In [12]:
df=df.sort_values(by='ds')

In [13]:
df.set_index('ds', inplace=True)


In [14]:
df = df.resample('D').fillna(method='ffill')

In [15]:
df.reset_index(inplace=True)

In [16]:
df.head(10)

ds       y
0 2000-01-03  1592.2
1 2000-01-04  1638.7
2 2000-01-05  1595.8
3 2000-01-06  1617.6
4 2000-01-07  1613.3
5 2000-01-08  1613.3
6 2000-01-09  1613.3
7 2000-01-10  1632.9
8 2000-01-11  1572.5
9 2000-01-12  1624.8

#Train test split

In [17]:
df_train=df.iloc[:len(df)-365]
df_test= df.iloc[len(df)-365:]

#Training the model

In [18]:
m= Prophet()
m.fit(df_train)

INFO:prophet:Disabling daily seasonality. Run prophet with daily_seasonality=True to override this.
DEBUG:cmdstanpy:input tempfile: /tmp/tmpidjhamv6/8d8ynau7.json
DEBUG:cmdstanpy:input tempfile: /tmp/tmpidjhamv6/xtr7nzz1.json
DEBUG:cmdstanpy:idx 0
DEBUG:cmdstanpy:running CmdStan, num_threads: None
DEBUG:cmdstanpy:CmdStan args: ['/usr/local/lib/python3.9/dist-packages/prophet/stan_model/prophet_model.bin', 'random', 'seed=26065', 'data', 'file=/tmp/tmpidjhamv6/8d8ynau7.json', 'init=/tmp/tmpidjhamv6/xtr7nzz1.json', 'output', 'file=/tmp/tmpidjhamv6/prophet_models52n6whh/prophet_model-20230310132516.csv', 'method=optimize', 'algorithm=lbfgs', 'iter=10000']
13:25:16 - cmdstanpy - INFO - Chain [1] start processing
INFO:cmdstanpy:Chain [1] start processing
13:25:21 - cmdstanpy - INFO - Chain [1] done processing
INFO:cmdstanpy:Chain [1] done processing


In [19]:
future= m.make_future_dataframe(periods=365)

In [20]:
forecast= m.predict(future)

In [21]:
forecast.tail()

ds         trend    yhat_lower    yhat_upper   trend_lower  \
8449 2023-02-20  17106.285531  16064.167342  18238.189005  16695.938500   
8450 2023-02-21  17110.286334  16084.397915  18212.152043  16698.222550   
8451 2023-02-22  17114.287137  16117.305475  18293.391381  16698.568003   
8452 2023-02-23  17118.287941  16055.350651  18237.722109  16699.680160   
8453 2023-02-24  17122.288744  16137.849877  18281.105621  16700.136451   

       trend_upper  additive_terms  additive_terms_lower  \
8449  17531.626532       62.620027             62.620027   
8450  17540.144336       61.154623             61.154623   
8451  17548.902431       57.841667             57.841667   
8452  17556.339227       49.499044             49.499044   
8453  17561.815490       42.092088             42.092088   

      additive_terms_upper    weekly  weekly_lower  weekly_upper     yearly  \
8449             62.620027 -4.949350     -4.949350     -4.949350  67.569377   
8450             61.154623 -0.415104     -0.415104     -0.415104  61.569727   
8451             57.841667  2.864090      2.864090      2.864090  54.977578   
8452             49.499044  1.687097      1.687097      1.687097  47.811947   
8453             42.092088  1.991002      1.991002      1.991002  40.101086   

      yearly_lower  yearly_upper  multiplicative_terms  \
8449     67.569377     67.569377                   0.0   
8450     61.569727     61.569727                   0.0   
8451     54.977578     54.977578                   0.0   
8452     47.811947     47.811947                   0.0   
8453     40.101086     40.101086                   0.0   

      multiplicative_terms_lower  multiplicative_terms_upper          yhat  
8449                         0.0                         0.0  17168.905558  
8450                         0.0                         0.0  17171.440957  
8451                         0.0                         0.0  17172.128805  
8452                         0.0                         0.0  17167.786985  
8453                         0.0                         0.0  17164.380832

In [22]:
forecast[['ds', 'yhat', 'yhat_lower', 'yhat_upper']].tail()

ds          yhat    yhat_lower    yhat_upper
8449 2023-02-20  17168.905558  16064.167342  18238.189005
8450 2023-02-21  17171.440957  16084.397915  18212.152043
8451 2023-02-22  17172.128805  16117.305475  18293.391381
8452 2023-02-23  17167.786985  16055.350651  18237.722109
8453 2023-02-24  17164.380832  16137.849877  18281.105621

In [23]:
df_test.tail()

ds         y
8449 2023-02-20  17844.60
8450 2023-02-21  17826.70
8451 2023-02-22  17554.30
8452 2023-02-23  17511.25
8453 2023-02-24  17465.80

Prophet in-built visualization

In [24]:
from prophet.plot import plot_plotly, plot_components_plotly

In [26]:
plot_plotly(m ,forecast)

In [25]:
plot_components_plotly(m, forecast)

#Evaluation

In [30]:
from sklearn.metrics import mean_squared_error,mean_absolute_error
from statsmodels.tools.eval_measures import rmse

In [27]:
predictions = forecast.iloc[-365:]['yhat']

In [31]:
print("Mean squared error=",mean_squared_error(predictions,df_test['y']))
print("Mean absolute error=",mean_absolute_error(predictions,df_test['y']))
print("Root mean squared error= ", rmse(predictions,df_test['y']))

Mean squared error= 1222236.397439463
Mean absolute error= 973.6729666456089
Root mean squared error=  1105.5480077497598


# Changing parameters

In [32]:
n = Prophet(changepoint_range=0.95)

In [33]:
n.fit(df_train)
future1= n.make_future_dataframe(periods=365)
forecast1= n.predict(future1)
forecast1.tail()

INFO:prophet:Disabling daily seasonality. Run prophet with daily_seasonality=True to override this.
DEBUG:cmdstanpy:input tempfile: /tmp/tmpidjhamv6/_qzal8a4.json
DEBUG:cmdstanpy:input tempfile: /tmp/tmpidjhamv6/8aiw48pq.json
DEBUG:cmdstanpy:idx 0
DEBUG:cmdstanpy:running CmdStan, num_threads: None
DEBUG:cmdstanpy:CmdStan args: ['/usr/local/lib/python3.9/dist-packages/prophet/stan_model/prophet_model.bin', 'random', 'seed=64234', 'data', 'file=/tmp/tmpidjhamv6/_qzal8a4.json', 'init=/tmp/tmpidjhamv6/8aiw48pq.json', 'output', 'file=/tmp/tmpidjhamv6/prophet_modelrwo9io0c/prophet_model-20230310132730.csv', 'method=optimize', 'algorithm=lbfgs', 'iter=10000']
13:27:30 - cmdstanpy - INFO - Chain [1] start processing
INFO:cmdstanpy:Chain [1] start processing
13:27:36 - cmdstanpy - INFO - Chain [1] done processing
INFO:cmdstanpy:Chain [1] done processing


ds         trend    yhat_lower    yhat_upper   trend_lower  \
8449 2023-02-20  22858.551857  21636.076888  23947.151412  21675.490843   
8450 2023-02-21  22870.583525  21636.860635  23909.093536  21683.399933   
8451 2023-02-22  22882.615193  21726.044146  23906.407242  21691.309024   
8452 2023-02-23  22894.646860  21669.495122  24013.324157  21699.218114   
8453 2023-02-24  22906.678528  21653.260916  23999.683681  21707.190178   

       trend_upper  additive_terms  additive_terms_lower  \
8449  23762.171319       11.456054             11.456054   
8450  23778.505749       15.781697             15.781697   
8451  23793.894788       18.595693             18.595693   
8452  23809.121164       16.655075             16.655075   
8453  23824.343698       18.299504             18.299504   

      additive_terms_upper    weekly  weekly_lower  weekly_upper     yearly  \
8449             11.456054 -4.955203     -4.955203     -4.955203  16.411257   
8450             15.781697 -0.772168     -0.772168     -0.772168  16.553865   
8451             18.595693  2.153678      2.153678      2.153678  16.442015   
8452             16.655075  0.630472      0.630472      0.630472  16.024603   
8453             18.299504  3.044626      3.044626      3.044626  15.254877   

      yearly_lower  yearly_upper  multiplicative_terms  \
8449     16.411257     16.411257                   0.0   
8450     16.553865     16.553865                   0.0   
8451     16.442015     16.442015                   0.0   
8452     16.024603     16.024603                   0.0   
8453     15.254877     15.254877                   0.0   

      multiplicative_terms_lower  multiplicative_terms_upper          yhat  
8449                         0.0                         0.0  22870.007912  
8450                         0.0                         0.0  22886.365222  
8451                         0.0                         0.0  22901.210886  
8452                         0.0                         0.0  22911.301935  
8453                         0.0                         0.0  22924.978032

In [34]:
forecast1[['ds', 'yhat', 'yhat_lower', 'yhat_upper']].tail()

ds          yhat    yhat_lower    yhat_upper
8449 2023-02-20  22870.007912  21636.076888  23947.151412
8450 2023-02-21  22886.365222  21636.860635  23909.093536
8451 2023-02-22  22901.210886  21726.044146  23906.407242
8452 2023-02-23  22911.301935  21669.495122  24013.324157
8453 2023-02-24  22924.978032  21653.260916  23999.683681

In [35]:
df_test.tail()

ds         y
8449 2023-02-20  17844.60
8450 2023-02-21  17826.70
8451 2023-02-22  17554.30
8452 2023-02-23  17511.25
8453 2023-02-24  17465.80

In [36]:
plot_plotly(n ,forecast1)

In [39]:
predictions1 = forecast1.iloc[-365:]['yhat']

In [40]:
print("Mean squared error=",mean_squared_error(predictions1,df_test['y']))
print("Mean absolute error=",mean_absolute_error(predictions1,df_test['y']))
print("Root mean squared error= ", rmse(predictions1,df_test['y']))

Mean squared error= 12653178.2386458
Mean absolute error= 3412.806370137693
Root mean squared error=  3557.130618721472


# Parameter change

In [42]:
p = Prophet(interval_width=0.95)
model2 = p.fit(df_train)
future2= p.make_future_dataframe(periods=365)
forecast2= p.predict(future2)
forecast2.tail()

INFO:prophet:Disabling daily seasonality. Run prophet with daily_seasonality=True to override this.
DEBUG:cmdstanpy:input tempfile: /tmp/tmpidjhamv6/nogmd8wd.json
DEBUG:cmdstanpy:input tempfile: /tmp/tmpidjhamv6/bus965ji.json
DEBUG:cmdstanpy:idx 0
DEBUG:cmdstanpy:running CmdStan, num_threads: None
DEBUG:cmdstanpy:CmdStan args: ['/usr/local/lib/python3.9/dist-packages/prophet/stan_model/prophet_model.bin', 'random', 'seed=75297', 'data', 'file=/tmp/tmpidjhamv6/nogmd8wd.json', 'init=/tmp/tmpidjhamv6/bus965ji.json', 'output', 'file=/tmp/tmpidjhamv6/prophet_modelsjyg6_6n/prophet_model-20230310133043.csv', 'method=optimize', 'algorithm=lbfgs', 'iter=10000']
13:30:43 - cmdstanpy - INFO - Chain [1] start processing
INFO:cmdstanpy:Chain [1] start processing
13:30:48 - cmdstanpy - INFO - Chain [1] done processing
INFO:cmdstanpy:Chain [1] done processing


ds         trend    yhat_lower    yhat_upper   trend_lower  \
8449 2023-02-20  17106.285531  15474.866545  18992.757057  15928.244250   
8450 2023-02-21  17110.286334  15551.228266  19111.523607  15921.033890   
8451 2023-02-22  17114.287137  15461.126833  18905.750985  15913.823529   
8452 2023-02-23  17118.287941  15470.147170  19007.141459  15911.757169   
8453 2023-02-24  17122.288744  15394.980080  19210.150059  15909.964023   

       trend_upper  additive_terms  additive_terms_lower  \
8449  18412.045595       62.620027             62.620027   
8450  18420.112036       61.154623             61.154623   
8451  18428.178477       57.841667             57.841667   
8452  18436.244917       49.499044             49.499044   
8453  18444.311358       42.092088             42.092088   

      additive_terms_upper    weekly  weekly_lower  weekly_upper     yearly  \
8449             62.620027 -4.949350     -4.949350     -4.949350  67.569377   
8450             61.154623 -0.415104     -0.415104     -0.415104  61.569727   
8451             57.841667  2.864090      2.864090      2.864090  54.977578   
8452             49.499044  1.687097      1.687097      1.687097  47.811947   
8453             42.092088  1.991002      1.991002      1.991002  40.101086   

      yearly_lower  yearly_upper  multiplicative_terms  \
8449     67.569377     67.569377                   0.0   
8450     61.569727     61.569727                   0.0   
8451     54.977578     54.977578                   0.0   
8452     47.811947     47.811947                   0.0   
8453     40.101086     40.101086                   0.0   

      multiplicative_terms_lower  multiplicative_terms_upper          yhat  
8449                         0.0                         0.0  17168.905558  
8450                         0.0                         0.0  17171.440957  
8451                         0.0                         0.0  17172.128805  
8452                         0.0                         0.0  17167.786985  
8453                         0.0                         0.0  17164.380832

In [44]:
forecast2[['ds', 'yhat', 'yhat_lower', 'yhat_upper']].tail()

ds          yhat    yhat_lower    yhat_upper
8449 2023-02-20  17168.905558  15474.866545  18992.757057
8450 2023-02-21  17171.440957  15551.228266  19111.523607
8451 2023-02-22  17172.128805  15461.126833  18905.750985
8452 2023-02-23  17167.786985  15470.147170  19007.141459
8453 2023-02-24  17164.380832  15394.980080  19210.150059

In [45]:
df_test.tail()

ds         y
8449 2023-02-20  17844.60
8450 2023-02-21  17826.70
8451 2023-02-22  17554.30
8452 2023-02-23  17511.25
8453 2023-02-24  17465.80

In [46]:
predictions2 = forecast2.iloc[-365:]['yhat']

In [47]:
print("Mean squared error=",mean_squared_error(predictions2,df_test['y']))
print("Mean absolute error=",mean_absolute_error(predictions2,df_test['y']))
print("Root mean squared error= ", rmse(predictions2,df_test['y']))


Mean squared error= 1222236.397439463
Mean absolute error= 973.6729666456089
Root mean squared error=  1105.5480077497598


# Taking first model for final predictions

In [50]:
a= Prophet()
model_a=a.fit(df)
future_a= a.make_future_dataframe(periods=90)
forecast_a= a.predict(future_a)

INFO:prophet:Disabling daily seasonality. Run prophet with daily_seasonality=True to override this.
DEBUG:cmdstanpy:input tempfile: /tmp/tmpidjhamv6/84yopxlk.json
DEBUG:cmdstanpy:input tempfile: /tmp/tmpidjhamv6/sp9vljuu.json
DEBUG:cmdstanpy:idx 0
DEBUG:cmdstanpy:running CmdStan, num_threads: None
DEBUG:cmdstanpy:CmdStan args: ['/usr/local/lib/python3.9/dist-packages/prophet/stan_model/prophet_model.bin', 'random', 'seed=97943', 'data', 'file=/tmp/tmpidjhamv6/84yopxlk.json', 'init=/tmp/tmpidjhamv6/sp9vljuu.json', 'output', 'file=/tmp/tmpidjhamv6/prophet_modelb9biwkvn/prophet_model-20230310133511.csv', 'method=optimize', 'algorithm=lbfgs', 'iter=10000']
13:35:11 - cmdstanpy - INFO - Chain [1] start processing
INFO:cmdstanpy:Chain [1] start processing
13:35:27 - cmdstanpy - INFO - Chain [1] done processing
INFO:cmdstanpy:Chain [1] done processing


In [51]:
forecast_a.tail()

ds         trend    yhat_lower    yhat_upper   trend_lower  \
8539 2023-05-21  18527.249737  17476.978652  19178.272295  18507.277971   
8540 2023-05-22  18532.276853  17553.508083  19208.914608  18511.851843   
8541 2023-05-23  18537.303968  17518.640385  19230.128261  18515.045740   
8542 2023-05-24  18542.331084  17519.661634  19319.804798  18517.744514   
8543 2023-05-25  18547.358200  17588.528308  19354.723466  18522.522970   

       trend_upper  additive_terms  additive_terms_lower  \
8539  18530.555721     -150.429665           -150.429665   
8540  18536.407870     -147.896901           -147.896901   
8541  18543.399846     -135.943114           -135.943114   
8542  18548.762804     -127.150258           -127.150258   
8543  18555.447101     -121.808333           -121.808333   

      additive_terms_upper    weekly  weekly_lower  weekly_upper      yearly  \
8539           -150.429665 -1.628415     -1.628415     -1.628415 -148.801250   
8540           -147.896901 -5.065618     -5.065618     -5.065618 -142.831284   
8541           -135.943114  0.548116      0.548116      0.548116 -136.491231   
8542           -127.150258  2.762261      2.762261      2.762261 -129.912519   
8543           -121.808333  1.421903      1.421903      1.421903 -123.230236   

      yearly_lower  yearly_upper  multiplicative_terms  \
8539   -148.801250   -148.801250                   0.0   
8540   -142.831284   -142.831284                   0.0   
8541   -136.491231   -136.491231                   0.0   
8542   -129.912519   -129.912519                   0.0   
8543   -123.230236   -123.230236                   0.0   

      multiplicative_terms_lower  multiplicative_terms_upper          yhat  
8539                         0.0                         0.0  18376.820072  
8540                         0.0                         0.0  18384.379951  
8541                         0.0                         0.0  18401.360854  
8542                         0.0                         0.0  18415.180826  
8543                         0.0                         0.0  18425.549867

In [52]:
forecast_a[['ds', 'yhat', 'yhat_lower', 'yhat_upper']].tail()

ds          yhat    yhat_lower    yhat_upper
8539 2023-05-21  18376.820072  17476.978652  19178.272295
8540 2023-05-22  18384.379951  17553.508083  19208.914608
8541 2023-05-23  18401.360854  17518.640385  19230.128261
8542 2023-05-24  18415.180826  17519.661634  19319.804798
8543 2023-05-25  18425.549867  17588.528308  19354.723466

In [53]:
plot_plotly(a ,forecast_a)

In [54]:
plot_components_plotly(a, forecast_a)